In [2]:
import streamlit as st
import altair as alt
import polars as pl
import numpy as np
import sys
import plotly.express as px

In [3]:
sys.path.insert(0, '../Eleicoes/')

In [4]:
import standards as sdt_f

In [5]:
#disabilita o limite de 5.000 para processamento imposto pelo altair
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [6]:
def get_df(url):
    return pl.read_parquet(source=url)

In [7]:
def get_eleicao_18():
    return get_df(f"https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/main/Dados/Eleicoes/eleicao18_turno_01.parquet")

In [8]:
def get_eleicao_22():
    return get_df(f"https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/main/Dados/Eleicoes/eleicao22_turno_01.parquet")     

In [9]:
def get_municipios():
    return get_df(f"https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/main/Dados/Eleicoes/municipios.parquet") 

In [10]:
def get_capitais():
    return get_df(f"https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/main/Dados/Eleicoes/capitais.parquet")     

In [11]:
df_municipios = get_municipios()
df_capitais = get_capitais()

In [12]:
df_municipios.limit(1)

shape: (1, 8)
┌────────────┬─────────────┬─────────────────┬─────┬─────────┬──────────┬───────────┬─────┐
│ codigo_tse ┆ codigo_ibge ┆ nome            ┆ uf  ┆ capital ┆ latitude ┆ longitude ┆ ddd │
│ ---        ┆ ---         ┆ ---             ┆ --- ┆ ---     ┆ ---      ┆ ---       ┆ --- │
│ i64        ┆ i64         ┆ str             ┆ str ┆ i64     ┆ f64      ┆ f64       ┆ i64 │
╞════════════╪═════════════╪═════════════════╪═════╪═════════╪══════════╪═══════════╪═════╡
│ 93360      ┆ 5200050     ┆ Abadia de Goiás ┆ GO  ┆ 0       ┆ -16.7573 ┆ -49.4412  ┆ 62  │
└────────────┴─────────────┴─────────────────┴─────┴─────────┴──────────┴───────────┴─────┘

In [13]:
df_poll_18:pl.DataFrame = get_eleicao_18()
df_poll_18 = df_poll_18.filter(pl.col("CD_CARGO")==1)
df_poll_18 = df_poll_18.drop("NR_ZONA")
df_poll_18.limit(1)

shape: (1, 18)
┌─────────────┬────────────────┬───────┬───────┬───┬──────────────────┬─────────────────────┬───────────┬───────────┐
│ ANO_ELEICAO ┆ TP_ABRANGENCIA ┆ SG_UF ┆ SG_UE ┆ … ┆ POSIC_IDEOLOGICO ┆ SG_POSIC_IDEOLOGICO ┆ SG_REGIAO ┆ NM_REGIAO │
│ ---         ┆ ---            ┆ ---   ┆ ---   ┆   ┆ ---              ┆ ---                 ┆ ---       ┆ ---       │
│ i64         ┆ str            ┆ str   ┆ str   ┆   ┆ str              ┆ str                 ┆ str       ┆ str       │
╞═════════════╪════════════════╪═══════╪═══════╪═══╪══════════════════╪═════════════════════╪═══════════╪═══════════╡
│ 2018        ┆ F              ┆ SP    ┆ BR    ┆ … ┆ Centro Direita   ┆ CD                  ┆ SE        ┆ Sudeste   │
└─────────────┴────────────────┴───────┴───────┴───┴──────────────────┴─────────────────────┴───────────┴───────────┘

In [14]:
df_poll_22:pl.DataFrame = get_eleicao_22()
df_poll_22 = df_poll_22.filter(pl.col("CD_CARGO")==1)
df_poll_22 = df_poll_22.drop("NR_ZONA")
df_poll_22.limit(1)

shape: (1, 18)
┌─────────────┬────────────────┬───────┬───────┬───┬──────────────────┬─────────────────────┬───────────┬───────────┐
│ ANO_ELEICAO ┆ TP_ABRANGENCIA ┆ SG_UF ┆ SG_UE ┆ … ┆ POSIC_IDEOLOGICO ┆ SG_POSIC_IDEOLOGICO ┆ SG_REGIAO ┆ NM_REGIAO │
│ ---         ┆ ---            ┆ ---   ┆ ---   ┆   ┆ ---              ┆ ---                 ┆ ---       ┆ ---       │
│ i64         ┆ str            ┆ str   ┆ str   ┆   ┆ str              ┆ str                 ┆ str       ┆ str       │
╞═════════════╪════════════════╪═══════╪═══════╪═══╪══════════════════╪═════════════════════╪═══════════╪═══════════╡
│ 2022        ┆ F              ┆ RJ    ┆ BR    ┆ … ┆ Extrema Direita  ┆ ED                  ┆ SE        ┆ Sudeste   │
└─────────────┴────────────────┴───────┴───────┴───┴──────────────────┴─────────────────────┴───────────┴───────────┘

In [15]:
cols_list:list[str] = df_poll_18.columns
cols_list.remove("QT_VOTOS_VALIDOS")

In [16]:
df_poll_18 = df_poll_18.group_by(cols_list).sum()
df_poll_22 = df_poll_22.group_by(cols_list).sum()

In [17]:
df_poll_18 = df_poll_18.with_columns(
    pl.col("QT_VOTOS_VALIDOS").sum().over("CD_MUNICIPIO").alias("TOTAL_VOTOS_MUNIC"),
    (pl.col("QT_VOTOS_VALIDOS")/ pl.col("QT_VOTOS_VALIDOS").sum().over("CD_MUNICIPIO")).alias("PCT_VOTOS_MUNIC"),
)
df_poll_22 = df_poll_22.with_columns(
    pl.col("QT_VOTOS_VALIDOS").sum().over("CD_MUNICIPIO").alias("TOTAL_VOTOS_MUNIC"),
    (pl.col("QT_VOTOS_VALIDOS")/ pl.col("QT_VOTOS_VALIDOS").sum().over("CD_MUNICIPIO")).alias("PCT_VOTOS_MUNIC"),
)

In [18]:
#Filtrando para o PT, presidente e 2018
df_choropleth_a = df_poll_18.filter(pl.col("SG_PARTIDO")=="PT")
df_choropleth_b = df_poll_22.filter(pl.col("SG_PARTIDO")=="PT")

In [19]:
breaks:list[float] = [.25, .4, .55]
domain:list[str]=["<=25%", ">25%,<=40%", ">40%,<=55%",">55%"]

df_choropleth_a = (
    df_choropleth_a.select(["CD_MUNICIPIO","TOTAL_VOTOS_MUNIC","QT_VOTOS_VALIDOS","PCT_VOTOS_MUNIC"])
    .with_columns(
        pl.col("PCT_VOTOS_MUNIC").cut(breaks, labels=domain).alias("PCT_VOTOS_LIMIT")        
    )
    .join(df_municipios, left_on="CD_MUNICIPIO", right_on="codigo_tse", how="inner")
    .drop(pl.col(["capital","ddd"]))     
)

df_choropleth_b = (
    df_choropleth_b.select(["CD_MUNICIPIO","TOTAL_VOTOS_MUNIC","QT_VOTOS_VALIDOS","PCT_VOTOS_MUNIC"])
    .with_columns(
        pl.col("PCT_VOTOS_MUNIC").cut(breaks, labels=domain).alias("PCT_VOTOS_LIMIT")        
    )
    .join(df_municipios, left_on="CD_MUNICIPIO", right_on="codigo_tse", how="inner")
    .drop(pl.col(["capital","ddd"]))     
)

In [31]:
df_choropleth_a

shape: (5_570, 10)
┌──────────────┬───────────────────┬──────────────────┬─────────────────┬───┬─────────────────────────┬─────┬──────────┬───────────┐
│ CD_MUNICIPIO ┆ TOTAL_VOTOS_MUNIC ┆ QT_VOTOS_VALIDOS ┆ PCT_VOTOS_MUNIC ┆ … ┆ nome                    ┆ uf  ┆ latitude ┆ longitude │
│ ---          ┆ ---               ┆ ---              ┆ ---             ┆   ┆ ---                     ┆ --- ┆ ---      ┆ ---       │
│ i64          ┆ i64               ┆ i64              ┆ f64             ┆   ┆ str                     ┆ str ┆ f64      ┆ f64       │
╞══════════════╪═══════════════════╪══════════════════╪═════════════════╪═══╪═════════════════════════╪═════╪══════════╪═══════════╡
│ 14311        ┆ 11647             ┆ 6061             ┆ 0.520392        ┆ … ┆ Itapiúna                ┆ CE  ┆ -4.55516 ┆ -38.9281  │
│ 79995        ┆ 3975              ┆ 1041             ┆ 0.261887        ┆ … ┆ São Jorge do Patrocínio ┆ PR  ┆ -23.7647 ┆ -53.8823  │
│ 56626        ┆ 9253              ┆ 2049             ┆ 0.221442        ┆ … ┆ João Neiva              ┆ ES  ┆ -19.7577 ┆ -40.386   │
│ 28010        ┆ 12349             ┆ 5145             ┆ 0.416633        ┆ … ┆ Matriz de Camaragibe    ┆ AL  ┆ -9.15437 ┆ -35.5243  │
│ 86851        ┆ 54175             ┆ 11775            ┆ 0.217351        ┆ … ┆ Guaíba                  ┆ RS  ┆ -30.1086 ┆ -51.3233  │
│ …            ┆ …                 ┆ …                ┆ …               ┆ … ┆ …                       ┆ …   ┆ …        ┆ …         │
│ 91731        ┆ 5924              ┆ 1427             ┆ 0.240885        ┆ … ┆ Eldorado                ┆ MS  ┆ -23.7868 ┆ -54.2838  │
│ 28312        ┆ 4273              ┆ 2595             ┆ 0.607302        ┆ … ┆ Paulo Jacinto           ┆ AL  ┆ -9.36792 ┆ -36.3672  │
│ 49891        ┆ 2271              ┆ 763              ┆ 0.335975        ┆ … ┆ Pequeri                 ┆ MG  ┆ -21.8341 ┆ -43.1145  │
│ 68438        ┆ 23594             ┆ 1921             ┆ 0.081419        ┆ … ┆ Pedreira                ┆ SP  ┆ -22.7413 ┆ -46.8948  │
│ 96750        ┆ 4426              ┆ 1833             ┆ 0.414144        ┆ … ┆ Doverlândia             ┆ GO  ┆ -16.7188 ┆ -52.3189  │
└──────────────┴───────────────────┴──────────────────┴─────────────────┴───┴─────────────────────────┴─────┴──────────┴───────────┘

In [32]:
df_choropleth_b.filter(pl.col("nome")=="Corumbá")

shape: (1, 10)
┌──────────────┬───────────────────┬──────────────────┬─────────────────┬───┬─────────┬─────┬──────────┬───────────┐
│ CD_MUNICIPIO ┆ TOTAL_VOTOS_MUNIC ┆ QT_VOTOS_VALIDOS ┆ PCT_VOTOS_MUNIC ┆ … ┆ nome    ┆ uf  ┆ latitude ┆ longitude │
│ ---          ┆ ---               ┆ ---              ┆ ---             ┆   ┆ ---     ┆ --- ┆ ---      ┆ ---       │
│ i64          ┆ i64               ┆ i64              ┆ f64             ┆   ┆ str     ┆ str ┆ f64      ┆ f64       │
╞══════════════╪═══════════════════╪══════════════════╪═════════════════╪═══╪═════════╪═════╪══════════╪═══════════╡
│ 90638        ┆ 51383             ┆ 24073            ┆ 0.468501        ┆ … ┆ Corumbá ┆ MS  ┆ -19.0077 ┆ -57.651   │
└──────────────┴───────────────────┴──────────────────┴─────────────────┴───┴─────────┴─────┴──────────┴───────────┘

In [21]:
'''
    Desenha o mapa com as percentuais de votação do partido por cidade
'''

#df_capitais:pl.DataFrame,
facet_column:str="ANO_ELEICAO"
legend_sort:list[str]=domain[::-1]
facet_sort:list=[]
chart_title:str="" 
scaleDomain:list[str]=domain
scheme="inferno"
opacity=.6
rev_Schmeme:bool=False

# define choropleth scale
scale = alt.Scale(type="threshold", reverse=rev_Schmeme, domain=domain, scheme=scheme)

states = alt.Data(
  url='https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/refs/heads/main/Dados/Eleicoes/br_states.json',
  format=alt.DataFormat(property='features')
)
background_states:alt.vegalite.v5.api.Chart = (
  alt.Chart(alt.Data(states))
  .mark_geoshape(
      stroke='#fff',
      fillOpacity=0,
      strokeWidth=.03
  )
)

cities = alt.Data(
  url="https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/refs/heads/main/Dados/Eleicoes/geojs-100-mun_minifier.json",
  format=alt.DataFormat(property='features')
)

cities_map = alt.Chart(df_choropleth_b) \
.mark_geoshape(
    stroke="#fff", strokeWidth=.03
).project(
    type="equirectangular"
).encode(
  shape='geo:G',
  color=alt.Color("PCT_VOTOS_LIMIT:N",
      scale=scale,
      legend=alt.Legend(
        #orient="bottom",
        titleAnchor='middle',
        title="Percentual de Votos",
        #direction="horizontal"
        type="symbol",
        symbolSize=400,
        #symbolOpacity=.7,
        symbolStrokeWidth=0,
        symbolType="square",
        values=legend_sort
      )
  ),
  tooltip=[
      alt.Tooltip('uf:N', title='Estado'),
      alt.Tooltip('nome:N', title="Município"),
      alt.Tooltip("TOTAL_VOTOS_MUNIC:Q", format=",d", title="Votos Totais Município"),
      alt.Tooltip("QT_VOTOS_VALIDOS:Q",format=",d", title="Votos no Partido"),
      alt.Tooltip("PCT_VOTOS_MUNIC:Q", format=".2%", title="% Votos"),
  ]
).transform_lookup(
  lookup='codigo_ibge',
  from_=alt.LookupData(cities, key="properties.id"),
  as_='geo'
).properties(width=600)

alt.layer(background_states, cities_map)

alt.LayerChart(...)

In [46]:
breaks = [-.1, -.01, .01, .1]
domain=["<-10%", ">-10% e <=-1%", ">-1%,<=1%",">1% e <=10%", ">10%"]

In [47]:
df_choropleth_diff_a = (
    df_choropleth_a.rename({
        "TOTAL_VOTOS_MUNIC":"TOTAL_VOTOS_MUNIC_18",
        "QT_VOTOS_VALIDOS":"QT_VOTOS_VALIDOS_18",
        "PCT_VOTOS_MUNIC":"PCT_VOTOS_MUNIC_18"
    }).drop(["codigo_ibge", "nome",	"uf", "latitude","longitude"])
)

df_choropleth_diff_b=df_choropleth_b.rename({
    "TOTAL_VOTOS_MUNIC":"TOTAL_VOTOS_MUNIC_22",
    "QT_VOTOS_VALIDOS":"QT_VOTOS_VALIDOS_22",
    "PCT_VOTOS_MUNIC":"PCT_VOTOS_MUNIC_22"
})

In [49]:
df_choropleth_diff = (
  df_choropleth_diff_a
  .join(df_choropleth_diff_b, on="CD_MUNICIPIO", how="inner")
  .with_columns(
      (pl.col("PCT_VOTOS_MUNIC_22")-pl.col("PCT_VOTOS_MUNIC_18")).alias("PCT_DIFF"),
      (pl.col("QT_VOTOS_VALIDOS_22")-pl.col("QT_VOTOS_VALIDOS_18")).alias("QT_DIFF")
  ).with_columns(
    pl.col("PCT_DIFF").cut(breaks, labels=domain).alias("PCT_VOTOS_LIMIT")
  )
)

In [54]:
'''
Plota as diferenças de votos percentuais entre dois anos
'''
def choropleth_diff_votting(df_poll_diff:pl.DataFrame, df_capitais:pl.DataFrame, 
  chart_title:str, scaleDomain:list[str]=[-.01, .01, .05], 
  legend_sort:list[str]=[],
  scheme="inferno", rev_Schmeme:bool=False,
  opacity=.7, 
  tooltip_title_22:list[str]=["Total Votos Munic. 2022","Total Votos Part. 2022", "Perc. Votos Part. 2022"], 
  tooltip_title_18:list[str]=["Total Votos Munic. 2018","Total Votos Part. 2018", "Perc. Votos Part. 2018"],
  legend_title:str='')->alt.vegalite.v5.api.Chart:

  scale = alt.Scale(type="threshold", reverse=rev_Schmeme, domain=scaleDomain, scheme=scheme)

  states = alt.Data(
      url='https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/refs/heads/main/Dados/Eleicoes/br_states.json',
      format=alt.DataFormat(property='features')
  )
  background_states:alt.vegalite.v5.api.Chart = (
      alt.Chart(alt.Data(states))
      .mark_geoshape(
          stroke='#000',
          fillOpacity=0,
          strokeWidth=0
      )
  )

  cities = alt.Data(
      url="https://raw.githubusercontent.com/perferctstorm/DiscursoOdioEleicoes/refs/heads/main/Dados/Eleicoes/geojs-100-mun_minifier.json",
      format=alt.DataFormat(property='features')
  )

  cities_map =(alt.Chart(df_poll_diff)
    .mark_geoshape(
        stroke="#000", strokeWidth=.03, fillOpacity=opacity
    ).project(
        type="equirectangular"
    ).encode(
      shape='geo:G',
      color=alt.Color("PCT_VOTOS_LIMIT:N",
          scale=scale,
          legend=alt.Legend(
            titleAnchor='middle',
            title=f"{legend_title}",
            type="symbol",
            symbolSize=400,
            #symbolOpacity=.8,
            symbolStrokeWidth=0,
            symbolType="square",
            values=legend_sort
          )
      ),
      tooltip=[
          alt.Tooltip('uf:N', title='Estado'),
          alt.Tooltip('nome:N', title="Município"),
          alt.Tooltip("TOTAL_VOTOS_MUNIC_22:Q", format=",d", title=f"{tooltip_title_22[0]}"),
          alt.Tooltip("TOTAL_VOTOS_MUNIC_18:Q", format=",d", title=f"{tooltip_title_18[0]}"),
          alt.Tooltip("QT_VOTOS_VALIDOS_22:Q", format=",d", title=f"{tooltip_title_22[1]}"),
          alt.Tooltip("QT_VOTOS_VALIDOS_18:Q", format=",d", title=f"{tooltip_title_18[1]}"),
          alt.Tooltip("PCT_VOTOS_MUNIC_22:Q", format=".2%", title=f"{tooltip_title_22[2]}"),
          alt.Tooltip("PCT_VOTOS_MUNIC_18:Q",format=".2%", title=f"{tooltip_title_18[2]}"),
          alt.Tooltip("QT_DIFF:Q", format=",d", title="Diff. Votos"),
          alt.Tooltip("PCT_DIFF:Q", format=".2%", title="Diff. % Votos")      
    ]
    ).transform_lookup(
      lookup='codigo_ibge',
      from_=alt.LookupData(cities, key="properties.id"),
      as_='geo'
    ).properties(width=600)
  ) 

  return (
    alt.layer(background_states, cities_map)
    .properties(title=f"{chart_title}")
    .configure_title(anchor="middle")
  )

In [61]:
choropleth_diff_votting(
    df_choropleth_diff, df_capitais,
    scaleDomain=domain,
    chart_title="",
    opacity=1.,
    legend_sort=domain[::-1],
    tooltip_title_22=["Total Votos Munic. 2022","Tot Votos PT 2022", "Perc. Votos PT 2022"],
    tooltip_title_18=["Total Votos Munic. 2018","Tot Votos PT 2018", "Perc. Votos PT 2018"]
).configure_legend(
  offset=-120,
)

alt.LayerChart(...)

In [5]:
import altair as alt
from vega_datasets import data

source = data.cars()

chart = alt.Chart(source).mark_circle().encode(
    x='Horsepower',
    y='Miles_per_Gallon',
    color='Origin',
).interactive()

chart

alt.Chart(...)